---
title: "sound"
execute:
  # echo: false
  freeze: auto  # re-render only when source changes
format:
  html:
    code-fold: true
    code-summary: "Show the code"
---

Sound source: [University of Iowa Electronic Music Studios](https://theremin.music.uiowa.edu/index.html)

Listen to these three notes on the piano

![](keyboard_3notes.png)

::: {.column-margin}
Image modified from: [piano-music-theory.com](https://piano-music-theory.com/2016/05/28/the-piano-keyboard/)
:::


A3
<audio controls="controls"><source src="files/Piano.mf.A3.aiff" type="audio/aiff" /></audio>  
A4 
<audio controls="controls"><source src="files/Piano.mf.A4.aiff" type="audio/aiff" /></audio>  
B4
<audio controls="controls"><source src="files/Piano.mf.B4.aiff" type="audio/aiff" /></audio>

In [2]:
#| code-summary: "import stuff"
import numpy as np
import matplotlib.pyplot as plt
import matplotlib as mpl
import pandas as pd
import aifc
from pandas.plotting import register_matplotlib_converters
register_matplotlib_converters()  # datetime converter for a matplotlib
import seaborn as sns
sns.set(style="ticks", font_scale=1.5)

import plotly.io as pio
pio.renderers.default = "plotly_mimetype+notebook_connected"
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
pio.templates.default = "presentation"
import math
import scipy
from scipy.io import wavfile

# %matplotlib widget

In [21]:
#| code-summary: "define useful functions"
def open_aiff(filename):
    data = aifc.open(filename)
    Nframes = data.getnframes()
    str_signal = data.readframes(Nframes)
    # d = np.fromstring(str_signal, numpy.short).byteswap()
    d = np.frombuffer(str_signal, dtype=np.int16).byteswap()
    # if there are two channels, take only one of them
    if data.getnchannels() == 2:
        d = d[::2]
    N = len(d)
    dt = 1.0 / data.getframerate()
    time = np.arange(N) * dt
    return time, d

def open_wav_return_fft(filename, max_freq=None):
    sample_rate, signal = wavfile.read(filename)
    time = np.arange(len(signal)) / sampling_rate
    dt = time[1] - time[0]
    N = len(time)
    signal = normalize(signal)
    fft = scipy.fft.fft(signal) / N
    k = scipy.fft.fftfreq(N, dt)
    fft_abs = np.abs(fft)
    if max_freq == None:
        max_freq = k.max()
    dk = 1 / (time.max() - time.min())
    n = int(max_freq/dk)
    return k[:n], fft_abs[:n]


def normalize(signal):
    return (signal - signal.mean()) / signal.std()

def fft_abs(signal, time, max_freq=None):
    dt = time[1] - time[0]
    N = len(time)
    fft = scipy.fft.fft(signal) / N
    k = scipy.fft.fftfreq(N, dt)
    fft_abs = np.abs(fft)
    if max_freq == None:
        max_freq = k.max()
    dk = 1 / (time.max() - time.min())
    n = int(max_freq/dk)
    return k[:n], fft_abs[:n]
    

In [22]:
#| code-summary: "load audio files"
tmin = 2.00
tmax = 2.20

timeA4, pianoA4 = open_aiff('files/Piano.mf.A4.aiff')
indices = np.where((timeA4 > tmin) & (timeA4 < tmax))
timeA4 = timeA4[indices]
pianoA4 = normalize(pianoA4[indices])

timeA3, pianoA3 = open_aiff('files/Piano.mf.A3.aiff')
indices = np.where((timeA3 > tmin) & (timeA3 < tmax))
timeA3 = timeA3[indices]
pianoA3 = normalize(pianoA3[indices])

timeB4, pianoB4 = open_aiff('files/Piano.mf.B4.aiff')
indices = np.where((timeB4 > tmin) & (timeB4 < tmax))
timeB4 = timeB4[indices]
pianoB4 = normalize(pianoB4[indices])

In [23]:
#| code-summary: "plot time series for 3 notes"
# blue, orange, green, red, purple, brown, pink, gray, olive, cyan = px.colors.qualitative.D3[:]

color_A3 = "#e7c535"
color_A4 = "#ff00c3"
color_B4 = "#327fce"

fig = make_subplots()

fig.add_trace(
    go.Scatter(x=list(timeA3),
               y=list(pianoA3),
               name='piano A3',
               line=dict(color=color_A3),
               visible='legendonly'),
)

fig.add_trace(
    go.Scatter(x=list(timeA4),
               y=list(pianoA4),
               name='piano A4',
               line=dict(color=color_A4),
               ),
)

fig.add_trace(
    go.Scatter(x=list(timeB4),
               y=list(pianoB4),
               name='piano B4',
               line=dict(color=color_B4),
               visible='legendonly'),
)

# Add range slider
fig.update_layout(
    title='3 notes on the piano',
    xaxis=dict(
        rangeslider={"visible":True},
        type="linear"
    ),
    legend={"orientation":"h",           # Horizontal legend
            "yanchor":"top",             # Anchor legend to the top
            "y":1.1,                    # Adjust vertical position
            "xanchor":"center",           # Anchor legend to the right
            "x":0.5,                       # Adjust horizontal position
           },
)

# Set y-axes titles
fig.update_yaxes(
    title_text="signal",
    range=[-3,3])
fig.update_xaxes(
    title_text="time (s)",)

* When we zoom in, both A3 and A4 have the same period, but different shapes.
* A4 and B4 have slightly different periods (A4 is longer).

## power spectrum

We can plot the absolute value of the Fourier transform of each signal, see below.

In [20]:
abs_fft_A4.max()

26175.95280463613

In [24]:
#| code-summary: "calculate fourier transform"
kA4, abs_fft_A4 = fft_abs(pianoA4, timeA4, max_freq=4e3)
kA3, abs_fft_A3 = fft_abs(pianoA3, timeA3, max_freq=4e3)
kB4, abs_fft_B4 = fft_abs(pianoB4, timeB4, max_freq=4e3)

In [25]:
#| code-summary: "plot power spectrum for 3 notes"

fig = make_subplots()

fig.add_trace(
    go.Scatter(x=list(kA3),
               y=list(abs_fft_A3),
               name='piano A3',
               line=dict(color=color_A3),
               visible='legendonly'),
)

fig.add_trace(
    go.Scatter(x=list(kA4),
               y=list(abs_fft_A4),
               name='piano A4',
               line=dict(color=color_A4),),
)

fig.add_trace(
    go.Scatter(x=list(kB4),
               y=list(abs_fft_B4),
               name='piano B4',
               line=dict(color=color_B4),
               visible='legendonly'),
)

# Add range slider
fig.update_layout(
    title='3 notes on the piano',
    legend={"orientation":"h",           # Horizontal legend
            "yanchor":"top",             # Anchor legend to the top
            "y":1.1,                    # Adjust vertical position
            "xanchor":"center",           # Anchor legend to the right
            "x":0.5,                       # Adjust horizontal position
           },
)

# Set y-axes titles
fig.update_yaxes(
    title_text="abs(FFT)",
    range=[-0.1,1])
fig.update_xaxes(
    title_text="frequency (Hz)",)

In [18]:
np.sum(abs_fft_A4) #* (kA4[1]-kA4[0])

160533.77179613346

In [11]:
kA4

array([   0.        ,    5.00056696,   10.00113392,   15.00170087,
         20.00226783,   25.00283479,   30.00340175,   35.0039687 ,
         40.00453566,   45.00510262,   50.00566958,   55.00623653,
         60.00680349,   65.00737045,   70.00793741,   75.00850437,
         80.00907132,   85.00963828,   90.01020524,   95.0107722 ,
        100.01133915,  105.01190611,  110.01247307,  115.01304003,
        120.01360698,  125.01417394,  130.0147409 ,  135.01530786,
        140.01587482,  145.01644177,  150.01700873,  155.01757569,
        160.01814265,  165.0187096 ,  170.01927656,  175.01984352,
        180.02041048,  185.02097743,  190.02154439,  195.02211135,
        200.02267831,  205.02324527,  210.02381222,  215.02437918,
        220.02494614,  225.0255131 ,  230.02608005,  235.02664701,
        240.02721397,  245.02778093,  250.02834789,  255.02891484,
        260.0294818 ,  265.03004876,  270.03061572,  275.03118267,
        280.03174963,  285.03231659,  290.03288355,  295.03345

We call the graph above a power spectrum. "Spectrum" refers to the frequencies, and "power" means that we square the signal. Strictly speaking, we see above the square root of the power spectrum, but I'll still call it power spectrum.

::: {.column-margin}
The energy associated with a wave is proportional to the square of the wave's amplitude. When we computed the `fft` of the signal, we divided it by `N`, which is akin to dividing by the whole time duration of the signal. For this reason we are dealing with power, which is energy / time. Finally, it should be noted that the square of a complex number $z=a+ib$ is given by

$$
|z|^2 = z\cdot z^*,
$$

where $z^*=a-ib$ is its complex conjugate:

$$
z\cdot z^* = (a+ib)(a-ib) = a^2 + b^2.
$$

:::

We call the lowest peak in the spectrum the fundamental frequency. Note that there are other high frequency peaks that follow the fundamental, at regular intervals. These are called overtones, and they are multiples of the fundamental frequency. The fundamental and the overtones are called together the harmonics.

![](crowhurst_basic_audio_vol1-23.jpg)

::: {.column-margin}
Image source: [N.H. Crowhurst](http://www.vias.org/crowhurstba/crowhurst_basic_audio_vol1_009.html)
:::

Probably, the most common tuning standard in western music is A440, meaning that the note corresponding to the A4 on the piano must have a fundamental frequency equal to 440 Hz. Zoom in and find out if the piano was "properly" tuned.

The A3 note has its fundamental frequency at half of that, namely 220 Hz. 

::: {.callout-note collapse="true" icon=false}
## {{< iconify fa music >}} Because there are 12 half-steps between A3 and A4, can you figure out a rule how to find the frequency of any note on the piano?

Dividing an octave in 12 equal half-steps is called "equal temperament". Multiplying the A3 frequency 12 times by an unknown factor $y$ should give us the frequency of A4:

$$
\begin{split}
220 \times y^{12} &= 440\\
y^{12} &= 2 \\
\therefore y &= \sqrt[12]{2}
\end{split}
$$
:::

We can now easily check out if the fundamental frequency for B3 as shown in the graph agrees with this rule:

In [9]:
#| code-summary: "calculate frequency for B4"
factor = 2**(1/12)
B4 = 440 * factor**2  # two half steps above A4
print(f"B4 = {B4:.2f} Hz")

B4 = 493.88 Hz


## timbre

| instrument | recording of A4 |  image |
|------|----------------------|--------|
| piano  | <audio controls="controls"><source src="files/piano-C4.wav" type="audio/wav" /></audio> | ![](https://upload.wikimedia.org/wikipedia/commons/5/55/Keyboard_of_grand_piano_-_Steinway_%26_Sons_%28Hamburg_factory%29.jpg){width="150px"} |
| flute | <audio controls="controls"><source src="files/flute-C4.wav" type="audio/wav" /></audio> | ![](https://upload.wikimedia.org/wikipedia/commons/thumb/b/bf/Western_Concert_Flute.jpg/640px-Western_Concert_Flute.jpg){width="150px"} |
| trumpet | <audio controls="controls"><source src="files/trumpet-C4.wav" type="audio/wav" /></audio> | ![](files/trumpet.png){width="150px"} |
| violin | <audio controls="controls"><source src="files/violin-C4.wav" type="audio/wav" /></audio> | ![](https://upload.wikimedia.org/wikipedia/commons/thumb/f/f4/German%2C_maple_Violin.JPG/640px-German%2C_maple_Violin.JPG){width="150px"} |


In [10]:
tmin = 1.00
tmax = 2.50

time_list = []
signal_list = []
instrument_list = ['flute', 'piano', 'trumpet', 'violin']
file_list = ['flute-C4.wav',
             'piano-C4.wav',
             'trumpet-C4.wav',
             'violin-C4.wav'
            ]

k_list = []
abs_fft_list = []
for i, filename in enumerate(file_list):
    k, abs_fft = open_wav_return_fft(f'files/{filename}', max_freq=10e3)
    k_list.append(k)
    abs_fft_list.append(abs_fft)


NameError: name 'sampling_rate' is not defined

In [ ]:
#| code-summary: "plot power spectrum for 3 notes"

fig = make_subplots()

for i, instrument in enumerate(file_list):
    fig.add_trace(
        go.Scatter(x=list(k_list[i]),
                y=list(abs_fft_list[i]),
                name=f'{instrument_list[i]}',
                # line=dict(color=color_A3),
                # visible='legendonly'
                ),
    )

# Add range slider
fig.update_layout(
    # title='3 notes on the piano',
    legend={"orientation":"h",           # Horizontal legend
            "yanchor":"top",             # Anchor legend to the top
            "y":1.1,                    # Adjust vertical position
            "xanchor":"center",           # Anchor legend to the right
            "x":0.5,                       # Adjust horizontal position
           },
)

# Set y-axes titles
fig.update_yaxes(
    title_text="abs(FFT)",
    range=[-0.05,0.4])
fig.update_xaxes(
    title_text="frequency (Hz)",)